## Scraping the wikipedia

### 1. Import libraries

In [1]:

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


### 2. Scrap data from Wikipedia page into a DataFrame

In [2]:
# get the response in the form of html
wikiurl="https://en.wikipedia.org/wiki/List_of_cities_in_India_by_population"
table_class="wikitable sortable jquery-tablesorter"
response=requests.get(wikiurl).text
response

'\n<!DOCTYPE html>\n<html class="client-nojs" lang="en" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>List of cities in India by population - Wikipedia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"3d0f3ebe-b01f-4d86-9296-0667bf53a1c9","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_cities_in_India_by_population","wgTitle":"List of cities in India by population","wgCurRevisionId":971165813,"wgRevisionId":971165813,"wgArticleId":4021386,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Pages with URL errors","All articles with dead external links","Articles with dead extern

In [3]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(response, 'html.parser')
indiatable=soup.find('table',{'class':"wikitable"})

In [4]:
df=pd.read_html(str(indiatable))

In [5]:
# convert list to dataframe
df=pd.DataFrame(df[0])

In [6]:
df.head()

Rank       City  Population(2011)[3] Population(2001)  \
0     1     Mumbai             12442373         11978450   
1     2      Delhi             11007835          9879172   
2     3  Bangalore              8436675          4301326   
3     4  Hyderabad              6809970          3637483   
4     5  Ahmedabad              5570585          3520085   

  State or union territory  
0              Maharashtra  
1                    Delhi  
2                Karnataka  
3                Telangana  
4                  Gujarat

In [8]:
# drop the unwanted columns
data = df.drop(["Rank", "Population(2001)"], axis=1)

In [10]:
# rename columns for ease
data = data.rename(columns={"City": "Neighborhood","State or union territory": "State","Population(2011)[3]": "Population"})
data.head()

Neighborhood  Population        State
0       Mumbai    12442373  Maharashtra
1        Delhi    11007835        Delhi
2    Bangalore     8436675    Karnataka
3    Hyderabad     6809970    Telangana
4    Ahmedabad     5570585      Gujarat

In [11]:
data.shape

(315, 3)

### 3. Get the geographical coordinates

In [12]:
# define a function to get coordinates
def get_latlng(neighborhood,state):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, {}, India'.format(neighborhood,state))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [13]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(x,y) for x,y in zip(data["Neighborhood"].tolist(),data["State"].tolist()) ]

In [14]:
print(coords)
print(len(coords))

[[18.940170000000023, 72.83483000000007], [28.634100000000046, 77.21689000000003], [12.966180000000065, 77.58690000000007], [17.394870000000026, 78.47076000000004], [23.027760000000058, 72.60027000000008], [13.083620000000053, 80.28252000000003], [22.570530000000076, 88.37124000000006], [21.185780000000022, 72.83679000000006], [18.504220000000032, 73.85302000000007], [26.925730000000044, 75.80659000000003], [26.85471000000007, 80.92135000000007], [26.43562000000003, 80.32986000000005], [21.157050000000027, 79.08217000000008], [22.716220000000078, 75.86512000000005], [19.200000000000045, 72.96667000000008], [23.26466000000005, 77.40518000000003], [17.719840000000033, 83.26278000000008], [18.618670000000066, 73.80375000000004], [25.601290000000063, 85.13751000000008], [22.30946000000006, 73.17993000000007], [28.662490000000048, 77.43777000000006], [30.907250000000033, 75.84919000000008], [27.192170000000033, 78.00007000000005], [19.995030000000042, 73.79647000000006], [28.39247000000006,

In [15]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])
# merge the coordinates into the original dataframe
data['Latitude'] = df_coords['Latitude']
data['Longitude'] = df_coords['Longitude']
data.head(10)

Neighborhood  Population        State  Latitude  Longitude
0       Mumbai    12442373  Maharashtra  18.94017   72.83483
1        Delhi    11007835        Delhi  28.63410   77.21689
2    Bangalore     8436675    Karnataka  12.96618   77.58690
3    Hyderabad     6809970    Telangana  17.39487   78.47076
4    Ahmedabad     5570585      Gujarat  23.02776   72.60027
5      Chennai     4681087   Tamil Nadu  13.08362   80.28252
6      Kolkata     4486679  West Bengal  22.57053   88.37124
7        Surat     4467797      Gujarat  21.18578   72.83679
8         Pune     3124458  Maharashtra  18.50422   73.85302
9       Jaipur     3046163    Rajasthan  26.92573   75.80659

In [16]:
#drop the state column as it is not required anymore
indf = data.drop("State", axis=1)
indf.head()

Neighborhood  Population  Latitude  Longitude
0       Mumbai    12442373  18.94017   72.83483
1        Delhi    11007835  28.63410   77.21689
2    Bangalore     8436675  12.96618   77.58690
3    Hyderabad     6809970  17.39487   78.47076
4    Ahmedabad     5570585  23.02776   72.60027

In [17]:
# save the DataFrame as CSV file
indf.to_csv("dataset.csv", index=False)

### 4. Create a map of India with neighborhoods superimposed on top

In [18]:
# get the coordinates of India
address = 'India'

geolocator = Nominatim(user_agent="newuser")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of India is {}, {}.'.format(latitude, longitude))

The geograpical coordinate of India is 22.3511148, 78.6677428.


In [19]:
# create map of India using latitude and longitude values
map_kl = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to map
for lat, lng, neighborhood in zip(indf['Latitude'], indf['Longitude'], indf['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_kl)  
    
map_kl

In [20]:
# save the map as HTML file
map_kl.save('map_india.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [21]:
# define Foursquare Credentials and Version
CLIENT_ID = '3AQL2V41IRW2YAJKPBVQO1TV12AXQRT5VY50KEKKAMF4G4IW' # your Foursquare ID
CLIENT_SECRET = 'IUNSO140I1TMQUQP1M5RHMIUWCP0YX1D1EYCOXDIE43I45PD' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3AQL2V41IRW2YAJKPBVQO1TV12AXQRT5VY50KEKKAMF4G4IW
CLIENT_SECRET:IUNSO140I1TMQUQP1M5RHMIUWCP0YX1D1EYCOXDIE43I45PD


#### Now, let's get the top 100 venues that are within a radius of 5 kilometers.

In [26]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(indf['Latitude'], indf['Longitude'], indf['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]["groups"][0]['items']
    #print(results)
    #break
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [27]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(5793, 7)


Neighborhood  Latitude  Longitude         VenueName  VenueLatitude  \
0       Mumbai  18.94017   72.83483       Royal China      18.938715   
1       Mumbai  18.94017   72.83483         Starbucks      18.932190   
2       Mumbai  18.94017   72.83483   Britannia & Co.      18.934683   
3       Mumbai  18.94017   72.83483  Food for Thought      18.932031   
4       Mumbai  18.94017   72.83483  Wankhede Stadium      18.938792   

   VenueLongitude       VenueCategory  
0       72.832933  Chinese Restaurant  
1       72.833959         Coffee Shop  
2       72.840183    Parsi Restaurant  
3       72.831667                Café  
4       72.825944      Cricket Ground

#### Let's check how many venues were returned for each neighorhood

In [28]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                                  
Adoni                                6          6          6              6   
Agartala                             9          9          9              9   
Agra                                38         38         38             38   
Ahmedabad                          100        100        100            100   
Ahmednagar                           4          4          4              4   
Aizawl                               5          5          5              5   
Ajmer                               10         10         10             10   
Akola                                4          4          4              4   
Alappuzha                           26         26         26             26   
Aligarh                              4          4          4              4   
Allahabad                           18         18         18             18   
Alwar                                5          5          5              5   
Amaravati                            5          5          5              5   
Ambala                               4          4          4              4   
Ambarnath                           10         10         10             10   
Ambattur                            59         59         59             59   
Amravati                             5          5          5              5   
Amritsar                            50         50         50             50   
Amroha                               6          6          6              6   
Anand                               22         22         22             22   
Anantapur                            4          4          4              4   
Arrah                                4          4          4              4   
Asansol                              4          4          4              4   
Aurangabad                          29         29         29             29   
Aurangabad[36]                       5          5          5              5   
Avadi                                5          5          5              5   
Bahraich                             7          7          7              7   
Ballia                               5          5          5              5   
Bally                                6          6          6              6   
Bangalore                          100        100        100            100   
Baranagar                           17         17         17             17   
Barasat                              5          5          5              5   
Bardhaman                            4          4          4              4   
Bareilly                             4          4          4              4   
Bathinda                             8          8          8              8   
Begusarai                            4          4          4              4   
Belgaum                             21         21         21             21   
Bellary                             10         10         10             10   
Berhampore                           5          5          5              5   
Bettiah[30]                          3          3          3              3   
Bhagalpur                            9          9          9              9   
Bhalswa Jahangir Pur                23         23         23             23   
Bharatpur                            6          6          6              6   
Bhatpara                             2          2          2              2   
Bhavnagar                           15         15         15             15   
Bhilai                               8          8          8              8   
Bhilwara                             4          4          4              4   
Bhimavaram                           8          8          8              8   
Bhind                                4          4          4              4   
B

#### Let's find out how many unique categories can be curated from all the returned venues

In [29]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 277 uniques categories.


In [30]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:]

array(['Chinese Restaurant', 'Coffee Shop', 'Parsi Restaurant', 'Café',
       'Cricket Ground', 'Scenic Lookout', 'Indian Restaurant',
       'Ice Cream Shop', 'Seafood Restaurant', 'Bakery', 'Art Gallery',
       'Beach', 'Hotel', 'Boutique', 'Pub', 'Dessert Shop',
       'Gym / Fitness Center', 'History Museum', 'Pizza Place',
       'Italian Restaurant', 'Diner', 'Gift Shop', 'Lounge', 'Nightclub',
       'Middle Eastern Restaurant', 'Fast Food Restaurant',
       'Deli / Bodega', 'New American Restaurant',
       'Performing Arts Venue', 'Theater', 'Monument / Landmark',
       'Asian Restaurant', 'Market', 'Bar', 'Japanese Restaurant',
       'Restaurant', 'Thai Restaurant', 'Music Venue', 'Juice Bar', 'Spa',
       'Brewery', 'Golf Course', 'Bookstore', 'Park', 'Donut Shop',
       'Sandwich Place', 'Club House', 'Stadium', "Men's Store",
       'Vegetarian / Vegan Restaurant', 'Plaza',
       'South Indian Restaurant', 'Clothing Store', 'Food Truck',
       'Bistro', 'Molecular

In [31]:
# looking for the most populary venue category
count = venues_df.groupby(['VenueCategory']).count() 
count.sort_values(["Neighborhood"], inplace=True,ascending=False)
count

Neighborhood  Latitude  Longitude  \
VenueCategory                                                                 
Indian Restaurant                                  679       679        679   
Hotel                                              397       397        397   
Café                                               340       340        340   
Pizza Place                                        281       281        281   
Fast Food Restaurant                               265       265        265   
Train Station                                      192       192        192   
Multiplex                                          177       177        177   
Ice Cream Shop                                     168       168        168   
Coffee Shop                                        164       164        164   
Shopping Mall                                      163       163        163   
Restaurant                                         140       140        140   
Bakery                                             129       129        129   
ATM                                                122       122        122   
Clothing Store                                      90        90         90   
Sandwich Place                                      88        88         88   
Chinese Restaurant                                  86        86         86   
Asian Restaurant                                    78        78         78   
Snack Place                                         69        69         69   
Vegetarian / Vegan Restaurant                       68        68         68   
Dessert Shop                                        63        63         63   
Movie Theater                                       62        62         62   
Italian Restaurant                                  57        57         57   
Bus Station                                         56        56         56   
Department Store                                    56        56         56   
Lounge                                              50        50         50   
Park                                                46        46         46   
Historic Site                                       38        38         38   
Market                                              38        38         38   
Diner                                               38        38         38   
Juice Bar                                           38        38         38   
Resort                                              33        33         33   
Bar                                                 33        33         33   
Food Court                                          33        33         33   
BBQ Joint                                           31        31         31   
Breakfast Spot                                      31        31         31   
Bookstore                                           30        30         30   
Motorcycle Shop                                     29        29         29   
Tea Room                                            27        27         27   
Fried Chicken Joint                                 27        27         27   
Pub                                                 27        27         27   
History Museum                                      26        26         26   
Gym                                                 26        26         26   
Electronics Store                                   25        25         25   
Donut Shop                                          24        24         24   
Platform                                            24        24         24   
Hotel Bar                                           24        24         24   
Plaza                                               24        24         24   
Scenic Lookout                                      23        23         23   
Seafood Restaurant                                  20        20         20   
Convenience S

In [32]:
# check if the results contain "Hotel"
"Hotel" in venues_df['VenueCategory'].unique()

True

### 6. Analyze Each Neighborhood

In [33]:
# one hot encoding
in_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
in_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [in_onehot.columns[-1]] + list(in_onehot.columns[:-1])
in_onehot = in_onehot[fixed_columns]

print(in_onehot.shape)
in_onehot.head()


(5793, 278)


Neighborhoods  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0        Mumbai    0                  0               0                  0   
1        Mumbai    0                  0               0                  0   
2        Mumbai    0                  0               0                  0   
3        Mumbai    0                  0               0                  0   
4        Mumbai    0                  0               0                  0   

   Airport  Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0        0             0               0                0                 0   
1        0             0               0                0                 0   
2        0             0               0                0                 0   
3        0             0               0                0                 0   
4        0             0               0                0                 0   

   American Restaurant  Andhra Restaurant  Antique Shop  Arcade  Art Gallery  \
0                    0                  0             0       0            0   
1                    0                  0             0       0            0   
2                    0                  0             0       0            0   
3                    0                  0             0       0            0   
4                    0                  0             0       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Assisted Living  \
0           0                    0                 0                0   
1           0                    0                 0                0   
2           0                    0                 0                0   
3           0                    0                 0                0   
4           0                    0                 0                0   

   Astrologer  Athletics & Sports  Australian Restaurant  Auto Garage  \
0           0                   0                      0            0   
1           0                   0                      0            0   
2           0                   0                      0            0   
3           0                   0                      0            0   
4           0                   0                      0            0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Basketball Court  Beach  \
0          0           0       0     0    0                 0      0   
1          0           0       0     0    0                 0      0   
2          0           0       0     0    0                 0      0   
3          0           0       0     0    0                 0      0   
4          0           0       0     0    0                 0      0   

   Bed & Breakfast  Beer Garden  Bengali Restaurant  Bistro  Board Shop  \
0                0            0                   0       0           0   
1                0            0                   0       0           0   
2                0            0                   0       0           0   
3                0            0                   0       0           0   
4                0            0                   0       0           0   

   Boarding House  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0               0              0          0                 0         0   
1               0              0          0                 0         0   
2               0              0          0                 0         0   
3               0              0          0                 0         0   
4               0              0          0                 0         0   

   Bowling Alley  Breakfast Spot  Brewery  Buffet  Burger Joint  \
0              0               0        0       0             0   
1              0               0        0       0             0   
2              0               0        0       0             0   
3              0               0        0       0             0   
4              0             

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [34]:
in_grouped = in_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(in_grouped.shape)
in_grouped

(308, 278)


Neighborhoods       ATM  Accessories Store  \
0                           Adoni  0.000000           0.000000   
1                        Agartala  0.222222           0.000000   
2                            Agra  0.000000           0.000000   
3                       Ahmedabad  0.000000           0.000000   
4                      Ahmednagar  0.000000           0.000000   
5                          Aizawl  0.000000           0.000000   
6                           Ajmer  0.000000           0.000000   
7                           Akola  0.000000           0.000000   
8                       Alappuzha  0.000000           0.000000   
9                         Aligarh  0.000000           0.000000   
10                      Allahabad  0.000000           0.000000   
11                          Alwar  0.000000           0.000000   
12                      Amaravati  0.200000           0.000000   
13                         Ambala  0.000000           0.000000   
14                      Ambarnath  0.000000           0.000000   
15                       Ambattur  0.000000           0.000000   
16                       Amravati  0.000000           0.000000   
17                       Amritsar  0.000000           0.000000   
18                         Amroha  0.333333           0.000000   
19                          Anand  0.000000           0.000000   
20                      Anantapur  0.000000           0.000000   
21                          Arrah  0.250000           0.000000   
22                        Asansol  0.000000           0.000000   
23                     Aurangabad  0.000000           0.000000   
24                 Aurangabad[36]  0.000000           0.000000   
25                          Avadi  0.000000           0.000000   
26                       Bahraich  0.285714           0.000000   
27                         Ballia  0.200000           0.000000   
28                          Bally  0.000000           0.000000   
29                      Bangalore  0.000000           0.000000   
30                      Baranagar  0.000000           0.000000   
31                        Barasat  0.000000           0.000000   
32                      Bardhaman  0.000000           0.250000   
33                       Bareilly  0.000000           0.250000   
34                       Bathinda  0.000000           0.000000   
35                      Begusarai  0.500000           0.000000   
36                        Belgaum  0.000000           0.000000   
37                        Bellary  0.000000           0.000000   
38                     Berhampore  0.400000           0.200000   
39                    Bettiah[30]  0.000000           0.000000   
40                      Bhagalpur  0.000000           0.000000   
41           Bhalswa Jahangir Pur  0.000000           0.000000   
42                      Bharatpur  0.000000           0.000000   
43                       Bhatpara  0.500000           0.000000   
44                      Bhavnagar  0.000000           0.000000   
45                         Bhilai  0.250000           0.000000   
46                       Bhilwara  0.000000           0.000000   
47                     Bhimavaram  0.000000           0.000000   
48                          Bhind  0.250000           0.000000   
49                       Bhiwandi  0.000000           0.000000   
50                        Bhiwani  0.285714           0.000000   
51                         Bhopal  0.000000           0.000000   
52                    Bhubaneswar  0.000000           0.000000   
53                       Bhusawal  0.200000           0.000000   
54                          Bidar  0.000000           0.000000   
55                   Bihar Sharif  0.250000           0.000000   
56                        Bijapur  0.000000           0.000000   
57                        Bikaner  0.000000           0.000000   
58                       Bilaspur  0.000000           0.000000   
59                         Bokaro  1.000000           0.0000

In [35]:
len(in_grouped[in_grouped["Hotel"] > 0.00])

126

#### Create a new DataFrame for Train Station data only

In [36]:
in_train = in_grouped[["Neighborhoods","Hotel"]]
in_train.head()

Neighborhoods     Hotel
0         Adoni  0.000000
1      Agartala  0.222222
2          Agra  0.236842
3     Ahmedabad  0.080000
4    Ahmednagar  0.000000

### 7. Cluster Neighborhoods

#### Run k-means to cluster the neighborhoods in Indian Cities into 3 clusters.

In [37]:
# set number of clusters
kclusters = 3

kl_clustering = in_train.drop(["Neighborhoods"], 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 1, 0, 0, 2, 1, 0, 0, 0])

In [38]:
# create a new dataframe that includes the cluster.
in_merged = in_train.copy()

# add clustering labels
in_merged["Cluster Labels"] = kmeans.labels_

In [39]:
in_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
in_merged.head()

Neighborhood     Hotel  Cluster Labels
0        Adoni  0.000000               0
1     Agartala  0.222222               1
2         Agra  0.236842               1
3    Ahmedabad  0.080000               0
4   Ahmednagar  0.000000               0

In [40]:
# merge in_grouped with india_data to add latitude/longitude for each neighborhood
in_merged = in_merged.join(indf.set_index("Neighborhood"), on="Neighborhood")

print(in_merged.shape)
in_merged.head() # check the last columns!

(308, 6)


Neighborhood     Hotel  Cluster Labels  Population  Latitude  Longitude
0        Adoni  0.000000               0      166537  15.63333   77.28333
1     Agartala  0.222222               1      399688  23.82920   91.29058
2         Agra  0.236842               1     1585704  27.19217   78.00007
3    Ahmedabad  0.080000               0     5570585  23.02776   72.60027
4   Ahmednagar  0.000000               0      350905  19.09208   74.73832

In [41]:
# sort the results by Cluster Labels
print(in_merged.shape)
in_merged.sort_values(["Cluster Labels"], inplace=True)
in_merged

(308, 6)


Neighborhood     Hotel  Cluster Labels  Population  \
0                           Adoni  0.000000               0      166537   
187                     Moradabad  0.000000               0      872575   
189                        Morena  0.000000               0      200482   
190                  Motihari[31]  0.000000               0      125183   
191                        Mumbai  0.040000               0    12442373   
192                        Munger  0.000000               0      213303   
193                 Muzaffarnagar  0.000000               0      392451   
194                   Muzaffarpur  0.000000               0      351838   
195               Mysore[7][8][9]  0.010000               0      920550   
196                        Nadiad  0.000000               0      218095   
197                        Nagaon  0.000000               0      148496   
199                        Nagpur  0.032258               0     2405665   
200                       Naihati  0.000000               0      217900   
201                        Nanded  0.000000               0      550564   
202                       Nandyal  0.000000               0      200516   
185                   Miryalaguda  0.000000               0      109891   
203                   Nangloi Jat  0.041667               0      205596   
205                        Nashik  0.054054               0     1486053   
206                   Navi Mumbai  0.020000               0     1120547   
207               Nellore[15][16]  0.055556               0      600869   
208                     New Delhi  0.090000               0      249998   
209                     Nizamabad  0.000000               0      310467   
210                         Noida  0.037037               0      642381   
211                  North Dumdum  0.000000               0      253625   
213                          Orai  0.000000               0      187137   
215                          Pali  0.000000               0      229956   
216                    Pallavaram  0.050000               0      215417   
217                     Panchkula  0.031250               0      211355   
218                      Panihati  0.000000               0      383522   
219                       Panipat  0.000000               0      294150   
220                        Panvel  0.030303               0      180020   
204                  Narasaraopet  0.000000               0      116250   
221                      Parbhani  0.000000               0      307191   
184                Mira-Bhayandar  0.000000               0      814655   
180                           Mau  0.000000               0      279060   
141                     Kamarhati  0.000000               0      336579   
142                        Kanpur  0.000000               0     2765348   
145                    Karimnagar  0.000000               0      260899   
147                       Katihar  0.000000               0      164937   
148                        Kavali  0.000000               0      104000   
149                       Khammam  0.000000               0      305000   
150                       Khandwa  0.000000               0      200738   
151                     Kharagpur  0.000000               0      207604   
152              Khora, Ghaziabad  0.000000               0      190400   
306              Warangal[11][12]  0.000000               0      830281   
154                Kishanganj[32]  0.000000               0      105782   
156                      Kolhapur  0.062500               0      549283   
157                       Kolkata  0.058140               0     4486679   
158                        Kollam  0.029412               0      349033   
183                       Mehsana  0.000000               0      184991   
159                         Korba  0.000000               0      363210   
161                      Kottayam  0.068966               0      172878   
162                     Kozhikode  0.033333   

#### Finally, let's visualize the resulting clusters

In [42]:
# create map
import numpy as np
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=5)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(in_merged['Latitude'], in_merged['Longitude'], in_merged['Neighborhood'], in_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [43]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

### 8. Examine Clusters

#### Cluster-0

In [44]:
in_merged.loc[in_merged['Cluster Labels'] == 0]


Neighborhood     Hotel  Cluster Labels  Population   Latitude  \
0                    Adoni  0.000000               0      166537  15.633330   
187              Moradabad  0.000000               0      872575  28.838930   
189                 Morena  0.000000               0      200482  26.490520   
190           Motihari[31]  0.000000               0      125183  26.657380   
191                 Mumbai  0.040000               0    12442373  18.940170   
192                 Munger  0.000000               0      213303  25.365560   
193          Muzaffarnagar  0.000000               0      392451  29.470290   
194            Muzaffarpur  0.000000               0      351838  26.123990   
195        Mysore[7][8][9]  0.010000               0      920550  12.955880   
196                 Nadiad  0.000000               0      218095  22.700000   
197                 Nagaon  0.000000               0      148496  26.349490   
199                 Nagpur  0.032258               0     2405665  21.157050   
200                Naihati  0.000000               0      217900  22.895760   
201                 Nanded  0.000000               0      550564  19.155660   
202                Nandyal  0.000000               0      200516  15.470330   
185            Miryalaguda  0.000000               0      109891  16.860950   
203            Nangloi Jat  0.041667               0      205596  28.678650   
205                 Nashik  0.054054               0     1486053  19.995030   
206            Navi Mumbai  0.020000               0     1120547  19.032620   
207        Nellore[15][16]  0.055556               0      600869  14.439790   
208              New Delhi  0.090000               0      249998  28.630950   
209              Nizamabad  0.000000               0      310467  18.686152   
210                  Noida  0.037037               0      642381  28.533420   
211           North Dumdum  0.000000               0      253625  22.685200   
213                   Orai  0.000000               0      187137  25.986650   
215                   Pali  0.000000               0      229956  25.772760   
216             Pallavaram  0.050000               0      215417  12.976110   
217              Panchkula  0.031250               0      211355  30.704570   
218               Panihati  0.000000               0      383522  22.696340   
219                Panipat  0.000000               0      294150  29.390050   
220                 Panvel  0.030303               0      180020  18.998210   
204           Narasaraopet  0.000000               0      116250  16.236600   
221               Parbhani  0.000000               0      307191  19.260790   
184         Mira-Bhayandar  0.000000               0      814655  19.274130   
180                    Mau  0.000000               0      279060  25.938540   
141              Kamarhati  0.000000               0      336579  23.582730   
142                 Kanpur  0.000000               0     2765348  26.435620   
145             Karimnagar  0.000000               0      260899  18.437170   
147                Katihar  0.000000               0      164937  25.538520   
148                 Kavali  0.000000               0      104000  14.912880   
149                Khammam  0.000000               0      305000  17.250870   
150                Khandwa  0.000000               0      200738  21.821220   
151              Kharagpur  0.000000               0      207604  22.328100   
152       Khora, Ghaziabad  0.000000               0      190400  28.662490   
306       Warangal[11][12]  0.000000               0      830281  17.406700   
154         Kishanganj[32]  0.000000               0      105782  26.102650   
156               Kolhapur  0.062500               0      549283  16.704460   
157                Kolkata  0.058140               0     4486679  22.570530   
158                 Kollam  0.029412               0      349033   8.886890   
183                Mehsana  0.000000               0      184991

#### Cluster-1

In [45]:
in_merged.loc[in_merged['Cluster Labels'] == 1]

Neighborhood     Hotel  Cluster Labels  Population  Latitude  \
143              Karaikudi  0.166667               1      106714  10.07416   
293                Udaipur  0.184615               1      451735  24.58700   
155                  Kochi  0.123596               1      601574   9.93601   
11                   Alwar  0.200000               1      315310  27.55608   
305    Visakhapatnam[a][5]  0.131579               1     1728128  17.71984   
1                 Agartala  0.222222               1      399688  23.82920   
275  Surendranagar Dudhrej  0.200000               1      177851  22.75513   
124                 Jaipur  0.300000               1     3046163  26.92573   
2                     Agra  0.236842               1     1585704  27.19217   
23              Aurangabad  0.172414               1     1175116  19.87010   
144          Karawal Nagar  0.166667               1      224666  28.72750   
130               Jamnagar  0.166667               1      529308  22.46919   
131             Jamshedpur  0.200000               1      631364  22.78150   
20               Anantapur  0.250000               1      261004  14.68365   
289           Tirupati[21]  0.294118               1      374260  13.63194   
134                 Jhansi  0.125000               1      507293  25.44858   
139               Kakinada  0.181818               1      443028  16.93333   
288            Tirunelveli  0.181818               1      473637   8.72640   
6                    Ajmer  0.200000               1      542580  26.46553   
17                Amritsar  0.140000               1     1132383  31.63347   
146                 Karnal  0.111111               1      286974  29.69009   
300               Varanasi  0.250000               1     1201815  25.33289   
135                Jodhpur  0.220588               1     1033918  26.26691   
21                   Arrah  0.250000               1      261099  25.55821   
85                    Durg  0.142857               1      268679  21.19914   
267                Solapur  0.166667               1      951558  17.65804   
89                  Etawah  0.250000               1      256838  26.77780   
198              Nagercoil  0.111111               1      224849   8.19389   
212                 Ongole  0.333333               1      204746  15.50599   
214              Ozhukarai  0.250000               1      300028  12.05600   
94              Gandhidham  0.200000               1      248705  23.08758   
188                  Morbi  0.111111               1      194947  22.80777   
186               Mirzapur  0.166667               1      233691  25.13432   
227            Pondicherry  0.154762               1      241773  11.92993   
182                 Meerut  0.111111               1     1305429  28.99860   
58                Bilaspur  0.142857               1      330106  22.08333   
235    Rajahmundry[19][20]  0.117647               1      419818  16.99609   
56                 Bijapur  0.250000               1      326360  16.82879   
29               Bangalore  0.110000               1     8436675  12.96618   
176                  Malda  0.200000               1      205521  25.01094   
179                Mathura  0.200000               1      349336  27.49186   
173                Madurai  0.122807               1     1017865   9.92417   
118          Hubli–Dharwad  0.173913               1      943788  15.35044   
263               Siliguri  0.105263               1      509709  26.73244   
115                 Hospet  0.200000               1      206167  15.26883   
38              Berhampore  0.200000               1      195223  24.10042   
259                Shimoga  0.142857               1      322428  13.94477   
258                 Shimla  0.181818               1      169578  31.10321   
165                Kurnool  0.142857               1      325300  15.82548   
253                 Satara  0.166667               1      326789  17.68333   
47              Bhimavaram  0.125000

#### Cluster-2

In [46]:
in_merged.loc[in_merged['Cluster Labels'] == 2]

Neighborhood     Hotel  Cluster Labels  Population  \
42                      Bharatpur  0.666667               2      252109   
242  Raurkela Industrial Township  0.571429               2      210317   
103                          Guna  0.500000               2      180935   
5                          Aizawl  0.400000               2      291822   
57                        Bikaner  0.444444               2      647804   
164                    Kumbakonam  0.500000               2      140056   
245                      Rourkela  0.500000               2      552734   
181                   Medininagar  0.500000               2      120325   

     Latitude  Longitude  
42   27.21087   77.48154  
242  22.22234   84.86267  
103  24.64643   77.31090  
5    23.73670   92.71460  
57   28.01647   73.31184  
164  10.95945   79.37878  
245  22.22972   84.86077  
181  24.03899   84.07681

#### cluster label - 0 seems to have least number of hotels within the radius of 5KM, With further and careful analysis perfect locations for building a new hotel in each city can be decided based on the cluster map above

#### From the cluster map above , In all of India north eastern cities are favourable locations for building a new Hotel